# Cimiano Chap. 2: Preliminaries

## Fig 2.3


In [1]:
fig_2_3 = """
@prefix wnid: <http://wordnet-rdf.princeton.edu/rdf/id/> .
@prefix wn: <http://wordnet-rdf.princeton.edu/ontology#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .

wnid:06422547-n rdfs:label "book"@en ;
wn:partOfSpeech wn:noun;
wn:hyponym wnid:06423235-n , wnid:06423396-n .
"""

https://rdflib.readthedocs.io/en/stable/gettingstarted.html

In [5]:
# !pip install rdflib

In [4]:
from rdflib import Graph

In [6]:
# create a Graph
g = Graph()

# parse from string
g.parse(data = fig_2_3, format = 'ttl')

<Graph identifier=N9f5b4e0e32da4673a4809dd8115ca541 (<class 'rdflib.graph.Graph'>)>

In [ ]:
len(g)

In [7]:
# Loop through each triple in the graph (subj, pred, obj)
for subj, pred, obj in g:
    print(subj, pred, obj)


http://wordnet-rdf.princeton.edu/rdf/id/06422547-n http://wordnet-rdf.princeton.edu/ontology#hyponym http://wordnet-rdf.princeton.edu/rdf/id/06423396-n
http://wordnet-rdf.princeton.edu/rdf/id/06422547-n http://wordnet-rdf.princeton.edu/ontology#hyponym http://wordnet-rdf.princeton.edu/rdf/id/06423235-n
http://wordnet-rdf.princeton.edu/rdf/id/06422547-n http://wordnet-rdf.princeton.edu/ontology#partOfSpeech http://wordnet-rdf.princeton.edu/ontology#noun
http://wordnet-rdf.princeton.edu/rdf/id/06422547-n http://www.w3.org/2000/01/rdf-schema#label book


In [8]:
# Print the number of "triples" in the Graph
print(f"Graph g has {len(g)} statements.")

Graph g has 4 statements.


In [9]:
# Print out the entire Graph in the RDF Turtle format
print(g.serialize(format="turtle"))

@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix wn: <http://wordnet-rdf.princeton.edu/ontology#> .
@prefix wnid: <http://wordnet-rdf.princeton.edu/rdf/id/> .

wnid:06422547-n rdfs:label "book"@en ;
    wn:hyponym wnid:06423235-n,
        wnid:06423396-n ;
    wn:partOfSpeech wn:noun .




In [13]:
# https://rdflib.readthedocs.io/en/stable/intro_to_parsing.html#saving-rdf
print(g.serialize(format="json-ld"))

[
  {
    "@id": "http://wordnet-rdf.princeton.edu/rdf/id/06422547-n",
    "http://wordnet-rdf.princeton.edu/ontology#hyponym": [
      {
        "@id": "http://wordnet-rdf.princeton.edu/rdf/id/06423235-n"
      },
      {
        "@id": "http://wordnet-rdf.princeton.edu/rdf/id/06423396-n"
      }
    ],
    "http://wordnet-rdf.princeton.edu/ontology#partOfSpeech": [
      {
        "@id": "http://wordnet-rdf.princeton.edu/ontology#noun"
      }
    ],
    "http://www.w3.org/2000/01/rdf-schema#label": [
      {
        "@language": "en",
        "@value": "book"
      }
    ]
  }
]


In [14]:
# Graph als ttl-Datei speichern
g.serialize(destination="../ttl/fig_2_3_rdflib.ttl")

<Graph identifier=N9f5b4e0e32da4673a4809dd8115ca541 (<class 'rdflib.graph.Graph'>)>

Download dieser ttl-Datei:

{download}`../ttl/fig_2_3_rdflib.ttl`

(Das ist Myst-Markdown. Dieses wird leider nicht in Jupyter Notebooks, sondern nur von jupyterbook korrekt ausgewertet.)

Wie kommmt diese Datei auf den Server? Jupyterbook kopiert diese Datei in ein "anonymes" Verzeichnis, das offensichtlich  nicht auf Persistenz ausgelegt ist. Ein `rsync` auf den Webserver kopiert auch dieses Verzeichnis mit. Wir haben das gemacht, und erhalten am 2023-03-22T0810:

* <http://jbusse.de/logd/_downloads/179ab022501f8adf259af127b10a66c1/fig_2_3_rdflib.ttl>

Falls wir eine schönere URL für unsere ttl-Datei haben wollen, müssen wir sie separat hochladen.)

Diese ttl-Datei, die wir gerade hochgeladen haben, können wir jetzt natürlich auch wieder über rdflib herunterladen und parsen:

In [15]:
g_online = Graph()
g_online.parse("http://jbusse.de/logd/_downloads/179ab022501f8adf259af127b10a66c1/fig_2_3_rdflib.ttl")

<Graph identifier=N31bc0d23c4594bf5a956fb42432de6f1 (<class 'rdflib.graph.Graph'>)>

In [16]:
len(g_online)

4

## 2.5 SPARQL

In [17]:
# Cimiano p.25
fig_2_9_q = """
SELECT ?label WHERE {
   <http://wordnet-rdf.princeton.edu/rdf/id/06422547-n>
      <http://www.w3.org/2000/01/rdf-schema#label>
         ?label.
} LIMIT 10
"""
for r in g.query(fig_2_9_q):
    print(r)

(rdflib.term.Literal('book', lang='en'),)


In [20]:
fig_2_10_q = """
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX wordnet: <http://wordnet-rdf.princeton.edu/rdf/id>
SELECT ?x ?label WHERE {
   ?x rdfs:label "book"@en .  # bei Cimiano nur "book": keine Ergebnisse!
} LIMIT 10"""
for r in g.query(fig_2_10_q):
    print(r)

(rdflib.term.URIRef('http://wordnet-rdf.princeton.edu/rdf/id/06422547-n'), None)


In [21]:
# motiviert durch
# https://rdflib.readthedocs.io/en/stable/gettingstarted.html#a-sparql-query-example
q = """
    PREFIX wnid: <http://wordnet-rdf.princeton.edu/rdf/id/>
    PREFIX wn: <http://wordnet-rdf.princeton.edu/ontology#>
    PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>

    SELECT ?p ?label
    WHERE {
        ?p wn:hyponym ?h .
        ?p rdfs:label ?label .
    }
"""
for r in g.query(q):
    print(r["p"],  r["label"])

http://wordnet-rdf.princeton.edu/rdf/id/06422547-n book
http://wordnet-rdf.princeton.edu/rdf/id/06422547-n book
